In [1]:
import IPython.display as IPDisplay

class TOC:
    __titleTemplate = "{titlePref} {title}"
    __tocTemplate = "{title}\n---\n{entries}"
    __entryTemplate = "{tabPref}{id}. {title}\n"
    
    def __init__(self, title, toc=[], tocLevel=2):
        self._toc = toc
        self._title = title
        self._level = tocLevel
    
    def title(self, *ids):
        prefix = "#"*min(self._level, (1+len(ids)))
        if len(ids) == 0:
            title = self._title
        else:
            entry = (None, self._toc)
            for i in ids:
                entry = entry[1][i]
            title = f"{'.'.join(str(1+i) for i in ids)}. {entry[0]}"
        return TOC.__titleTemplate.format(titlePref=prefix, title=title)
    
    def entries(self, toc, ids, depth=0):
        entries = ""
        tabPref = "\t"*depth
        for i, (title, subToc) in enumerate(toc):
            subEntries = ""
            if ids:
                if ids[0] == i:
                    title = f"__{title}__"
                    subEntries = self.entries(subToc, ids[1:], depth+1)
                elif ids[0] < 0:
                    subEntries = self.entries(subToc, ids[1:], depth+1)
            entry = TOC.__entryTemplate.format(tabPref=tabPref, id=i+1, title=title)
            entries = f"{entries}{entry}{subEntries}"
        return entries
    
    def display(self, *ids):
        title = self.title(*ids)
        if len(ids) == 0: ids = (-1,)*(self._level - 1)
        return TOC.__tocTemplate.format(title=title, entries=self.entries(self._toc, ids))

In [2]:
import pathlib

pathlib.Path("kernProfOut/").mkdir(exist_ok=True)
pathlib.Path("cProfOut/").mkdir(exist_ok=True)

In [3]:
__toc = TOC(
    "How to write faster python code", [(
    "Toy problem", [
        ("Quicksort algorithm", []),
        ("Code example", [
            ("First implementation", []),
            ("Test data (benchmark)", []),
            ("Driver program", []),
        ]),
    ]), (
    "Performance analysis (CPU)", [
        ("First step into profiling: cProfile", [
            ("Profile the code", []),
            ("Examine the stats", []),
            ("Review", []),
        ]),
        ("Opening the blackboxes: line_profiler", []),
    ]), (
    "From analysis to improvement: algorithmically", [
    ]), (
    "Optimising the constants", [
        ("Just In Time compilation", [
            ("Introducing Numba", []),
            ("Numpy, types and how they can help", []),
        ]),
        ("WTH is going on ?", [
            ("IS IT SLOWER !?", []),
            ("What just happened ?", []),
        ]),
    ]), (
    "Wrapping up", [
        ("Family picture", []),
        ("Do not reinvent the wheel", []),
    ]),
], tocLevel=1)

In [4]:
IPDisplay.Markdown(__toc.display())

# How to write faster python code
---
1. Toy problem
2. Performance analysis (CPU)
3. From analysis to improvement: algorithmically
4. Optimising the constants
5. Wrapping up


In [5]:
IPDisplay.Markdown(__toc.display(0))

# 1. Toy problem
---
1. __Toy problem__
	1. Quicksort algorithm
	2. Code example
2. Performance analysis (CPU)
3. From analysis to improvement: algorithmically
4. Optimising the constants
5. Wrapping up


In [6]:
IPDisplay.Markdown(f"""
{__toc.title(0, 0)}
---
> Given a __collection__ of __orderable__ elements, how to __sort__ them efficiently with regard to __computation time__ ?

There exists many different sorting algorithms. The fastest, most general purpose, and consequently the most commonly used is the __quicksort__ algorithm
""")


# 1.1. Quicksort algorithm
---
> Given a __collection__ of __orderable__ elements, how to __sort__ them efficiently with regard to __computation time__ ?

There exists many different sorting algorithms. The fastest, most general purpose, and consequently the most commonly used is the __quicksort__ algorithm


<div class="full-width">
  <div class="column" style="float: left; width: 25%; height: auto">
    <img src="https://upload.wikimedia.org/wikipedia/commons/6/6a/Sorting_quicksort_anim.gif" alt="QuicksortGIF">
  </div>
  <div class="column" style="float: right; width: 75%">
    <h3>Quicksort</h3>
    <ol>
        <li><u>Pick an element</u> from the collection, it is called the <b>pivot</b></li>
        <li><u>Partition</u> the elements in two subparts such that:
            <ul>
                <li>In the left part they are <b>smaller or equal</b> to the <b>pivot</b></li>
                <li>In the right part they are <b>greater</b> than the <b>pivot</b></li>
            </ul>
        </li>
        <li><u>Position the <b>pivot</b></u> between the two parts</li>
        <li><u>Repeat</u> this process on the subparts containing more than one element</li>
    </ol>
  </div>
</div>

In [7]:
IPDisplay.Markdown(__toc.display(0, 1))

# 1.2. Code example
---
1. __Toy problem__
	1. Quicksort algorithm
	2. __Code example__
		1. First implementation
		2. Test data (benchmark)
		3. Driver program
2. Performance analysis (CPU)
3. From analysis to improvement: algorithmically
4. Optimising the constants
5. Wrapping up


In [8]:
IPDisplay.Markdown(f"""
{__toc.title(0, 1, 0)}
---
""")


# 1.2.1. First implementation
---


In [9]:
def swap(array, i, j):
    array[i], array[j] = array[j], array[i]

def partition(array, pivot, low, high):
    i, j = low+1, low+1
    while j < high:
        while j < high and array[j] > pivot:
            j += 1
        if j < high:
            swap(array, i, j)
            i += 1
            j += 1
    return i - 1

In [10]:
IPDisplay.Markdown(f"""
{__toc.title(0, 1, 0)}
---
""")


# 1.2.1. First implementation
---


In [11]:
def quicksort(array, low=0, high=-1):
    if high < 0: high = len(array)
    pivot = array[low]  # choose an element
    pivotPos = partition(array, pivot, low, high)  # build partitions
    swap(array, pivotPos, low)  # place the pivot in between
    if pivotPos-low > 1:  # repeat on the left
        quicksort(array, low=low, high=pivotPos)
    if high-pivotPos > 2:  # repeat on the right
        quicksort(array, low=pivotPos+1, high=high)

In [12]:
IPDisplay.Markdown(f"""
{__toc.title(0, 1, 1)}
---
""")


# 1.2.2. Test data (benchmark)
---


In [13]:
from random import shuffle, randint

def produceArray(size, repeat):
    array = []
    for _ in range(repeat):
        start = randint(0, size//2)
        array.extend(range(start, start+size))
    shuffle(array)
    return array

arrays = [  # !! Use the same data across different runs
    produceArray(4000, 5)  # arrays of 20000 numbers 
    for _ in range(50)  # !! Have several (different) samples
]

#### Benchmark: Checklist
- Enough different samples (generalisation)
- But not too much to speed up development
    - Especially in early stages of the optimisation process
    - Depending on the problem, may not have the choice
- Same data across the different runs

<u>To compare the performances of different versions of your code, the data __must__ be the same !</u>
Otherwise, you cannot be certain if a gain/loss of speed is due to a change in the code or a change in the data

In [14]:
IPDisplay.Markdown(f"""
{__toc.title(0, 1, 2)}
---
""")


# 1.2.3. Driver program
---


In [15]:
nRuns = 10

def main():
    for _ in range(nRuns):  # !! Make several runs
        for array in arrays:
            # copy the data so the original is not altered
            cpArray = [o for o in array]
            # run your code
            quicksort(cpArray)
            # test the result (working code > fast code)
            assert all((cpArray[i] <= cpArray[i+1] for i in range(len(cpArray)-1)))

#### Driver program: Checklist
- Ensure repeatability of the runs
- Do not alter benchmark data
- __Don't break your code !__ (Test it)
- Make several runs to reduce the impact of the noise

#### Noise ?
- The performance of your code also depends on the environment in which it runs.
- For reasons out of your control, the system may suddenly run slower, hence impacting the performances.

Reduce the possible interferences if you can (shut down other programs, ...)

In [16]:
IPDisplay.Markdown(__toc.display(1))

# 2. Performance analysis (CPU)
---
1. Toy problem
2. __Performance analysis (CPU)__
	1. First step into profiling: cProfile
	2. Opening the blackboxes: line_profiler
3. From analysis to improvement: algorithmically
4. Optimising the constants
5. Wrapping up


## Profiling

>In software engineering, __profiling__ ("program profiling", "software profiling") is a form of dynamic program analysis that measures, for example, the space (memory) or time complexity of a program, the usage of particular instructions, or the __frequency and duration of function calls__. Most commonly, __profiling information serves to aid program optimization__, and more specifically, performance engineering.

(source: [Wikipedia](https://en.wikipedia.org/wiki/Profiling_(computer_programming)))

In [17]:
IPDisplay.Markdown(__toc.display(1, 0))

# 2.1. First step into profiling: cProfile
---
1. Toy problem
2. __Performance analysis (CPU)__
	1. __First step into profiling: cProfile__
		1. Profile the code
		2. Examine the stats
		3. Review
	2. Opening the blackboxes: line_profiler
3. From analysis to improvement: algorithmically
4. Optimising the constants
5. Wrapping up


In [18]:
IPDisplay.Markdown(f"""
{__toc.title(1, 0, 0)}
---
""")


# 2.1.1. Profile the code
---


__From within a python script :__

In [19]:
import cProfile

with cProfile.Profile() as pr:
    main()
    
# Generates a file containing statistics to be examined later :
pr.dump_stats("cProfOut/quicksort.stats")

__From the terminal :__

`python3 -m cProfile -o <cProfOut/quicksort.stats> <quicksort.py>`

In [20]:
IPDisplay.Markdown(f"""
{__toc.title(1, 0, 1)}
---
""")


# 2.1.2. Examine the stats
---


In [21]:
import pstats
import pandas as pd

prof = pstats.Stats("cProfOut/quicksort.stats")

#  The following code only serves to present the stats in a dataframe.
kCols = ['file', 'line', 'fn']
vCols = ['cc', 'ncalls', 'tottime', 'cumtime', 'callers']
data = {k: [] for k in vCols + kCols}

for k, v in prof.stats.items():
    for col, val in zip(kCols, k):
        data[col].append(val)

    for col, val in zip(vCols, v):
        data[col].append(val)
# --------------------------------------------------------------------

df = pd.DataFrame(data)
df = df.sort_values("cumtime", ascending=False)

In [22]:
df[["ncalls", "tottime", "cumtime", "fn"]][:8]

ncalls    tottime    cumtime                              fn
7          1   0.015210  32.772541                            main
9    7654920   3.272737  31.136494                       quicksort
8    7654920  20.264309  27.262684                       partition
6  101220550   7.599361   7.599361                            swap
0        500   0.431345   1.253280  <built-in method builtins.all>
3   10000000   0.821936   0.821936                       <genexpr>
2        500   0.367472   0.367472                      <listcomp>
1       1000   0.000172   0.000172  <built-in method builtins.len>

In [23]:
IPDisplay.Markdown(f"""
{__toc.title(1, 0, 1)}
---
""")


# 2.1.2. Examine the stats
---


In [24]:
# Translates the produced file in a call graph (.dot file)
!gprof2dot -f pstats cProfOut/quicksort.stats -o cProfOut/quicksortCallGraph.dot

# From the .dot file, draw the call graph in the desired format
!dot -Tpng cProfOut/quicksortCallGraph.dot > cProfOut/quicksortCallGraph.png
#dot -Tsvg cProfOut/quicksortCallGraph.dot > cProfOut/quicksortCallGraph.svg
#dot -Tjpg cProfOut/quicksortCallGraph.dot > cProfOut/quicksortCallGraph.jpg


![quicksortCallGraph](cProfOut/quicksortCallGraph.png)

In [25]:
IPDisplay.Markdown(f"""
{__toc.title(1, 0, 2)}
---
- Built-in python module
- Non-intrusive (from terminal)
- Great at pinpointing bottlenecks
- Very verbose. Needs sorting/filtering to extract useful information

__But no in-depth analysis of the code.__
Better used at high-level to highlight the slowest parts of a large project
""")


# 2.1.3. Review
---
- Built-in python module
- Non-intrusive (from terminal)
- Great at pinpointing bottlenecks
- Very verbose. Needs sorting/filtering to extract useful information

__But no in-depth analysis of the code.__
Better used at high-level to highlight the slowest parts of a large project


In [26]:
IPDisplay.Markdown(__toc.display(1, 1))

# 2.2. Opening the blackboxes: line_profiler
---
1. Toy problem
2. __Performance analysis (CPU)__
	1. First step into profiling: cProfile
	2. __Opening the blackboxes: line_profiler__
3. From analysis to improvement: algorithmically
4. Optimising the constants
5. Wrapping up


In [27]:
IPDisplay.Markdown(f"""
{__toc.title(1, 1)}
---
""")


# 2.2. Opening the blackboxes: line_profiler
---


In [28]:
import line_profiler as lp

pr = lp.LineProfiler()
pr.add_function(partition)
pr.add_function(quicksort)
prMain = pr(main)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/quicksort.lprof")

In [29]:
prof = lp.load_stats("kernProfOut/quicksort.lprof")

with open("kernProfOut/quicksort.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

#lp.show_text(prof.timings, prof.unit)

Instead of using `.add_function()`, one can mark functions directly inside the code
```python
@lp.profile
def f():
    ...

class C:
    
    @lp.profile
    def f(self):
        ...
```

In [30]:
with open("kernProfOut/quicksort.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [31]:
IPDisplay.Markdown(__toc.display(2))

# 3. From analysis to improvement: algorithmically
---
1. Toy problem
2. Performance analysis (CPU)
3. __From analysis to improvement: algorithmically__
4. Optimising the constants
5. Wrapping up


In [32]:
IPDisplay.Markdown(f"""
{__toc.title(2)}
---
- Write faster code by using fewer instructions
- Remove as much slow operations as possible

__WARNING !!__
The new code _must_ be functionally equivalent.
Remember the `assert` clause in the `main()` function ? __Test your code__
""")


# 3. From analysis to improvement: algorithmically
---
- Write faster code by using fewer instructions
- Remove as much slow operations as possible

__WARNING !!__
The new code _must_ be functionally equivalent.
Remember the `assert` clause in the `main()` function ? __Test your code__


In [33]:
def betterPartition(array, pivot, low, high):
    i = low+1
    for j in range(low+1, high):
        if array[j] <= pivot:
            swap(array, i, j)
            i += 1
    return i - 1

- No more comparisons `j < high`
- No more increment `j += 1`
    - (j is incremented in the `for` loop)
- One single loop

In [34]:
def betterQuicksort(array, low=0, high=-1):
    if high < 0:
        high = len(array)
    pivot = array[low]
    pivotPos = betterPartition(array, pivot, low, high)
    swap(array, pivotPos, low)
    if pivotPos-low > 1:
        betterQuicksort(array, low=low, high=pivotPos)
    if high-pivotPos > 2:
        betterQuicksort(array, low=pivotPos+1, high=high)
        
def betterMain():
    for _ in range(nRuns):
        for array in arrays:
            cpArray = [o for o in array]
            betterQuicksort(cpArray)
            assert all((cpArray[i] <= cpArray[i+1] for i in range(len(cpArray)-1)))

In [35]:
pr = lp.LineProfiler()
pr.add_function(betterPartition)
pr.add_function(betterQuicksort)
prMain = pr(betterMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/betterQuicksort.lprof")

In [36]:
prof = lp.load_stats("kernProfOut/betterQuicksort.lprof")

with open("kernProfOut/betterQuicksort.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

#lp.show_text(prof.timings, prof.unit)

In [37]:
with open("kernProfOut/betterQuicksort.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [38]:
IPDisplay.Markdown(f"""
{__toc.title(3)}
---
- Compile some heavily used functions
- Reduce the overhead by using low-level instructions instead of actual python code

__WARNING !!__
JIT compiling has a _once only_ overhead.
Use it only when it is worth it (a function used __a lot__ of times in your code)
""")


# 4. Optimising the constants
---
- Compile some heavily used functions
- Reduce the overhead by using low-level instructions instead of actual python code

__WARNING !!__
JIT compiling has a _once only_ overhead.
Use it only when it is worth it (a function used __a lot__ of times in your code)


In [39]:
IPDisplay.Markdown(__toc.display(3, 0))

# 4.1. Just In Time compilation
---
1. Toy problem
2. Performance analysis (CPU)
3. From analysis to improvement: algorithmically
4. __Optimising the constants__
	1. __Just In Time compilation__
		1. Introducing Numba
		2. Numpy, types and how they can help
	2. WTH is going on ?
5. Wrapping up


In [40]:
IPDisplay.Markdown(f"""
{__toc.title(3, 0, 0)}
---
""")


# 4.1.1. Introducing Numba
---


In [41]:
import numba as nb

@nb.jit(nopython=True)
def fasterSwap(array, i, j):
    array[i], array[j] = array[j], array[i]

Numba compiles python functions and runs them on a Low Level Virtual Machine (LLVM).

- `@numba.jit` marks a function to be compiled _Just In Time_
- `nopython=True` means that the function does not use python objects
    - Removes the overhead induced by python
    - But `array` is a python list !

We are dealing with simple int values, using a list is clearly overkill

In [42]:
IPDisplay.Markdown(f"""
{__toc.title(3, 0, 1)}
---
__Numpy__ is certainly the most widely used python library in research
- It is coded in C (hence compiled).
- It provides multidimensional arrays of __primitive types__
- It is meant for fast numerical manipulation of matrices, tensors, ...
- Used alone or with SciPy, matplotlib, TensorFlow, PyTorch, ...

Numpy arrays are considered as `nopython` by numba, solving our issue with almost no change in the code
""")


# 4.1.2. Numpy, types and how they can help
---
__Numpy__ is certainly the most widely used python library in research
- It is coded in C (hence compiled).
- It provides multidimensional arrays of __primitive types__
- It is meant for fast numerical manipulation of matrices, tensors, ...
- Used alone or with SciPy, matplotlib, TensorFlow, PyTorch, ...

Numpy arrays are considered as `nopython` by numba, solving our issue with almost no change in the code


In [43]:
def betterFasterPartition(array, pivot, low, high):
    i = low+1
    for j in range(low+1, high):
        if array[j] <= pivot:
            fasterSwap(array, i, j)
            i += 1
    return i - 1

def betterFasterQuicksort(array, low=0, high=-1):
    if high < 0:
        high = len(array)
    pivot = array[low]
    pivotPos = betterFasterPartition(array, pivot, low, high)
    fasterSwap(array, pivotPos, low)
    if pivotPos-low > 1:
        betterFasterQuicksort(array, low=low, high=pivotPos)
    if high-pivotPos > 2:
        betterFasterQuicksort(array, low=pivotPos+1, high=high)

In [44]:
import numpy as np

def betterFasterMain():
    for _ in range(nRuns):
        for array in arrays:
            cpArray = np.array(array, dtype=np.int32)
            betterFasterQuicksort(cpArray)
            assert all((cpArray[i] <= cpArray[i+1] for i in range(len(cpArray)-1)))

In [45]:
pr = lp.LineProfiler()
pr.add_function(betterFasterPartition)
pr.add_function(betterFasterQuicksort)
prMain = pr(betterFasterMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/betterFasterQuicksort.lprof")

In [46]:
prof = lp.load_stats("kernProfOut/betterFasterQuicksort.lprof")

with open("kernProfOut/betterFasterQuicksort.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

#lp.show_text(prof.timings, prof.unit)

In [47]:
with open("kernProfOut/betterFasterQuicksort.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [48]:
IPDisplay.Markdown(__toc.display(3, 1))

# 4.2. WTH is going on ?
---
1. Toy problem
2. Performance analysis (CPU)
3. From analysis to improvement: algorithmically
4. __Optimising the constants__
	1. Just In Time compilation
	2. __WTH is going on ?__
		1. IS IT SLOWER !?
		2. What just happened ?
5. Wrapping up


In [49]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1)}
---
- The compiled version version of swap did not speed up the process
- The purpose of compiling swap was to make it faster
- Is it possible that compiled python is slower ?
""")
# TODO : explain that python itself uses some jit under the hood on a line per line basis. Numba really shines thanks to inlining
#           So why fasterSwap and not swap inside jitted partition ? Because of the nopython part. If swap is a python fct, numba falls back in object mode


# 4.2. WTH is going on ?
---
- The compiled version version of swap did not speed up the process
- The purpose of compiling swap was to make it faster
- Is it possible that compiled python is slower ?


In [50]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1, 0)}
---
""")


# 4.2.1. IS IT SLOWER !?
---


In [51]:
def cmpJIT(array):
    swap(array, 0, 1)
    swap(array, 0, 1)
    swap(array, 0, 1)
    fasterSwap(array, 0, 1)
    fasterSwap(array, 0, 1)
    fasterSwap(array, 0, 1)
        
pr = lp.LineProfiler()
prCmpJIT = pr(cmpJIT)
prCmpJIT(np.arange(2))
pr.dump_stats("kernProfOut/cmpJIT.lprof")

prof = lp.load_stats("kernProfOut/cmpJIT.lprof")
with open("kernProfOut/cmpJIT.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

In [52]:
with open("kernProfOut/cmpJIT.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [53]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1, 0)}
---
It could. But why ?
> Under the hood, Python performs a JIT compilation of each line of code. When doing so, python translates directly in binary and does not use a LLVM
- What is the point, then ?
- When and how is JIT compilation useful ?
""")


# 4.2.1. IS IT SLOWER !?
---
It could. But why ?
> Under the hood, Python performs a JIT compilation of each line of code. When doing so, python translates directly in binary and does not use a LLVM
- What is the point, then ?
- When and how is JIT compilation useful ?


In [54]:
@nb.jit(nopython=True)
def betterFasterStrongerPartition(array, pivot, low, high):
    i = low+1
    for j in range(low+1, high):
        if array[j] <= pivot:
            fasterSwap(array, i, j)  # inlining numba swap
            i += 1
    return i - 1

def betterFasterStrongerQuicksort(array, low=0, high=-1):
    if high < 0:
        high = len(array)
    pivot = array[low]
    pivotPos = betterFasterStrongerPartition(array, pivot, low, high)
    fasterSwap(array, pivotPos, low)
    if pivotPos-low > 1:
        betterFasterStrongerQuicksort(array, low=low, high=pivotPos)
    if high-pivotPos > 2:
        betterFasterStrongerQuicksort(array, low=pivotPos+1, high=high)
        
def betterFasterStrongerMain():
    for _ in range(nRuns):
        for array in arrays:
            cpArray = np.array(array, dtype=np.int32)
            betterFasterStrongerQuicksort(cpArray)
            assert all((cpArray[i] <= cpArray[i+1] for i in range(len(cpArray)-1)))

In [55]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1, 1)}
---
""")


# 4.2.2. What just happened ?
---


In [56]:
pr = lp.LineProfiler()
pr.add_function(betterFasterStrongerQuicksort)
prMain = pr(betterFasterStrongerMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/betterFasterStrongerQuicksort.lprof")

In [57]:
prof = lp.load_stats("kernProfOut/betterFasterStrongerQuicksort.lprof")

with open("kernProfOut/betterFasterStrongerQuicksort.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

#lp.show_text(prof.timings, prof.unit)

In [58]:
with open("kernProfOut/betterFasterStrongerQuicksort.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [59]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1, 1)}
---
- What was said before remains true
    - JIT is useful for heavily used functions
- Numba shines when inlining compiled functions (even one-liners)
- It was useful to compile `swap` but only to use it in other compiled functions
- In doubt, always profile the JIT version of your code VS the original one
""")


# 4.2.2. What just happened ?
---
- What was said before remains true
    - JIT is useful for heavily used functions
- Numba shines when inlining compiled functions (even one-liners)
- It was useful to compile `swap` but only to use it in other compiled functions
- In doubt, always profile the JIT version of your code VS the original one


In [60]:
IPDisplay.Markdown(__toc.display(4))

# 5. Wrapping up
---
1. Toy problem
2. Performance analysis (CPU)
3. From analysis to improvement: algorithmically
4. Optimising the constants
5. __Wrapping up__
	1. Family picture
	2. Do not reinvent the wheel


In [61]:
with cProfile.Profile() as pr:
    for _ in range(nRuns):
        for array in arrays:
            cpArray = [o for o in array]
            quicksort(cpArray)
            cpArray = [o for o in array]
            betterQuicksort(cpArray)
            cpArray = np.array(array, dtype=np.int32)
            betterFasterQuicksort(cpArray)
            cpArray = np.array(array, dtype=np.int32)
            betterFasterStrongerQuicksort(cpArray)
            cpArray = [o for o in array]
            cpArray.sort()
    
# Generates a file containing statistics to be examined later :
pr.dump_stats("cProfOut/quicksortAll.stats")

In [62]:
IPDisplay.Markdown(f"""
{__toc.title(4, 0)}
---
""")


# 5.1. Family picture
---


In [63]:
# Translates the produced file in a call graph (.dot file)
!gprof2dot -f pstats cProfOut/quicksortAll.stats -o cProfOut/quicksortAllCallGraph.dot
!dot -Tpng cProfOut/quicksortAllCallGraph.dot > cProfOut/quicksortAllCallGraph.png


![quicksortAllCallGraph](cProfOut/quicksortAllCallGraph.png)

__Note:__ The compiled code is not shown on the picture

In [64]:
IPDisplay.Markdown(f"""
{__toc.title(4, 1)}
---
The sort method of a list is _WAAAAYY_ faster than anything presented during this talk
- Always ask yourself if what you are doing exists already
- In other words, make a "state of the art" of the existing solutions
- __Worse case scenario:__ you lost 2 hours looking for some library that does not exist
- __Best case scenario:__ you spent days learning to use a library but you saved weeks of coding/profiling
""")


# 5.2. Do not reinvent the wheel
---
The sort method of a list is _WAAAAYY_ faster than anything presented during this talk
- Always ask yourself if what you are doing exists already
- In other words, make a "state of the art" of the existing solutions
- __Worse case scenario:__ you lost 2 hours looking for some library that does not exist
- __Best case scenario:__ you spent days learning to use a library but you saved weeks of coding/profiling


In [65]:
#jupyter nbconvert --to slides CPUProfDemo.ipynb --TagRemovePreprocessor.remove_input_tags="{'hide-input'}" --TagRemovePreprocessor.remove_single_output_tags='hide-output' --no-prompt --SlidesExporter.reveal_number='c/t' --post serve